In [18]:
import pandas as pd

In [19]:
df = pd.read_csv('demanda_fixed.csv.gz',sep =';',compression='gzip')
#termina con unas lineas de log que hay que quitar
df = df.dropna()
df['instante'] = pd.to_datetime(df['instante'])

In [20]:
df.head()

FECHA linea cochelogico  parada            instante  viajeros  \
0  20170920     1           1     718 2017-09-20 06:31:13         1   
1  20170920     1           1     722 2017-09-20 06:32:26         1   
2  20170920     1           1     722 2017-09-20 06:32:28         1   
3  20170920     1           1    2307 2017-09-20 06:34:11         1   
4  20170920     1           1     451 2017-09-20 06:43:16         1   

                  nombre   latitude  longitude  
0              CARTAGENA  40.439570  -3.673786  
1        CARTAGENA-BEJAR  40.437135  -3.671116  
2        CARTAGENA-BEJAR  40.437135  -3.671116  
3  PLAZA DE SAN CAYETANO  40.433904  -3.670554  
4          METRO SERRANO  40.426055  -3.687923

In [21]:
#lineas con mas paradas
lineas_paradas = df[['linea','parada']].drop_duplicates().groupby('linea').count().sort('parada',ascending = False)
lineas_paradas.head()

parada
linea        
150        91
116        88
132        82
71         81
34         80

# Rutas de Bus

In [22]:
#devuelve 
def buslog(linea,cochelogico,coordinates = False):
    
    bus_ruta = df[(df['linea'] == linea) & (df['cochelogico'] == cochelogico)].sort('instante')
    parada = -1
    instante        = []
    paradas         = []
    viajeros_parada = []
    instantes       = []
    viajeros        = 0
    for index, row in bus_ruta.iterrows():
        if parada != row['parada']:
            #print parada,viajeros
            if parada != -1:
                viajeros_parada.append(viajeros)
                paradas.append(parada)
                instantes.append(row['instante'])
            viajeros = 0
            parada = int(row['parada'])
            
        viajeros += int(row['viajeros'])
    
    ruta = pd.DataFrame(zip(paradas,viajeros_parada,instantes),columns=('parada','viajeros','instante'))
    
    
    if coordinates:
    
        nombres_paradas = df[['parada','nombre','latitude','longitude']].drop_duplicates().set_index('parada')
        ruta = ruta.set_index('parada').join(nombres_paradas)
        
    ruta = ruta.set_index('instante').sort()
        
    return ruta

In [23]:
buslog(2,3).head()

parada  viajeros
instante                             
2017-09-20 06:31:12     186         1
2017-09-20 06:32:16     187         1
2017-09-20 06:35:21     188         1
2017-09-20 06:37:19     190         8
2017-09-20 06:39:29     192         1

In [24]:
buslog(2,3,True).head()

viajeros                                  nombre  \
instante                                                                
2017-09-20 06:31:12         1                          REINA VICTORIA   
2017-09-20 06:32:16         1  GUZMAN EL BUENO-SAN FRANCISCO DE SALES   
2017-09-20 06:35:21         1                              JUAN VIGON   
2017-09-20 06:37:19         8   GUZMAN EL BUENO-FERNANDEZ DE LOS RIOS   
2017-09-20 06:39:29         1                               ARGUELLES   

                      latitude  longitude  
instante                                   
2017-09-20 06:31:12  40.445816  -3.712419  
2017-09-20 06:32:16  40.442869  -3.712660  
2017-09-20 06:35:21  40.441543  -3.712830  
2017-09-20 06:37:19  40.435811  -3.713238  
2017-09-20 06:39:29  40.430962  -3.713626

In [25]:
import folium
#linea 2, coche 5
ruta = buslog(44,1,True)
#filtramos de 9 a 11
ruta = ruta.between_time('6:00','10:30')

center = ruta[['latitude','longitude']].mean()
m = folium.Map(location=[center[0], center[1]],zoom_start=13)
folium.PolyLine(ruta[['latitude','longitude']].values.tolist()).add_to(m)
m

# viajeros paradas

analizamos el número total de los viajeros 

In [26]:
#viajeros paradas
bus_time = df.set_index('instante').between_time('0:00','1:00')
viajeros_parada = bus_time.groupby('parada')[['viajeros']].sum().sort('viajeros',ascending=False)
viajeros_parada.head()

viajeros
parada          
41           143
42           141
4070          89
5443          79
69            79

In [27]:
#join con las coordenadas
viajeros_parada = viajeros_parada.join(df[['parada','latitude','longitude']].drop_duplicates().set_index('parada'))
viajeros_parada.head()

viajeros   latitude  longitude
parada                                
41           143  40.451414  -3.691073
42           141  40.451426  -3.690527
4070          89  40.419926  -3.720890
5443          79  40.418565  -3.692938
69            79  40.419697  -3.693539

In [28]:
viajeros_parada['viajeros_norm'] = viajeros_parada['viajeros']/viajeros_parada.max()['viajeros']
viajeros_parada.head()

viajeros   latitude  longitude  viajeros_norm
parada                                               
41           143  40.451414  -3.691073       1.000000
42           141  40.451426  -3.690527       0.986014
4070          89  40.419926  -3.720890       0.622378
5443          79  40.418565  -3.692938       0.552448
69            79  40.419697  -3.693539       0.552448

In [29]:
from folium.plugins import HeatMap

center = viajeros_parada[['latitude','longitude']].mean()
m = folium.Map(location=[center[0], center[1]],zoom_start=11)
HeatMap(data = viajeros_parada[['latitude','longitude','viajeros_norm']].values.tolist()).add_to(m)
m

# Timeline

In [30]:
densidadDia = []

#viajeros paradas
for hour in range(23):
    bus_time = df.set_index('instante').between_time("{:02d}:00".format(hour),"{:02d}:00".format((hour + 1) % 24))
    viajeros_parada = bus_time.groupby('parada')[['viajeros']].sum().sort('viajeros',ascending=False)
    #join con las coordenadas
    viajeros_parada = viajeros_parada.join(df[['parada','latitude','longitude']].drop_duplicates().set_index('parada'))
    #normalizacion
    viajeros_parada['viajeros_norm'] = viajeros_parada['viajeros']/viajeros_parada.max()['viajeros']
    
    densidadDia.append(viajeros_parada[['latitude','longitude','viajeros_norm']].values.tolist())

In [31]:
from folium.plugins import HeatMapWithTime

center = viajeros_parada[['latitude','longitude']].mean()
m = folium.Map(location=[center[0], center[1]],zoom_start=11)
HeatMapWithTime(data = densidadDia).add_to(m)
m

In [32]:
#save as html
m.save('../../vis/04_EMT_densidad/index.html')